<h3>使用資料: face_data</h3>

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegressionCV
import numpy as np
from sklearn.svm import SVC, LinearSVC
from sklearn.neural_network import MLPClassifier

<h3>函式說明: </h3>
將資料 X 和標籤 以80%、20%分成訓練集和測試集，並且進行標準化。<br>
利用主成分分析（PCA）將訓練集和測試集轉換為二維空間，並將轉換後的訓練集和測試集存儲在變數 Z_train 和 Z_test 中。<br>
利用邏輯回歸、支持向量機和多層感知機三種分類器，針對原始資料和 PCA 轉換後的資料分別進行評估，計算測試資料的準確度並將其存儲在相應的變數中。<br>
最後函數返回所有評估結果的陣列，包括原始資料的邏輯回歸、支持向量機和多層感知機的準確度，PCA 轉換後的資料的邏輯回歸、支持向量機和多層感知機的準確度。

In [2]:
def  classifier (X,y,dataname,h):
    data=dataname
    # Split data into training and testing data 7:3
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20) 
    # Standardize data
    scaler = StandardScaler()
    X_train_ = scaler.fit_transform(X_train)
    X_test_ = scaler.fit_transform(X_test)

#PCA
    pca = PCA(n_components = 2).fit(X_train_)
    Z_train = pca.transform(X_train_)
    Z_test = pca.transform(X_test_)

#LogisticRegression
    LR=np.zeros(3)
    LR_CV=np.zeros(3)
    LR_pca=np.zeros(3)
    LR_CV_pca=np.zeros(3)

    Cs = np.logspace(-5, 5, 20)
    opts = dict(tol = 1e-6, max_iter = int(1e6), verbose=1)
    solver = ['lbfgs','liblinear','newton-cg'] 
    for s in range(3):
        clf_original = LogisticRegression(solver = solver[s], **opts)
        clf_original.fit(X_train_, y_train)
        y_pred = clf_original.predict(X_test_)
        # 測 試 資 料 之 準 確 率 回 報
        LR[s]= accuracy_score(y_test, y_pred)

        clf_PCA = LogisticRegression(solver = solver[s], **opts)
        clf_PCA.fit(Z_train, y_train)
        LR_pca[s]=clf_PCA.score(Z_test, y_test)

 # SVM
    SVM=np.zeros((2,3))
    SVM_pca=np.zeros((2,3))
    C = 1 # SVM regularization parameter
    opts = [dict(C = C, tol = 1e-6, max_iter = int(1e6)),dict(C = C, decision_function_shape = 'ovo', tol = 1e-6, max_iter = int(1e6))]
    
    for i in range(2):
        for j in range(3):
            clf_svm = [SVC(kernel="linear", **opts[i]),\
            SVC(kernel="rbf", gamma=0.2, **opts[i]),\
             SVC(kernel="poly", degree=3, gamma="auto", **opts[i])]
             #LinearSVC(**opts[i]) ]

            clf_svm[j].fit(X_train, y_train)
            predictions = clf_svm[j].predict(X_test)
            SVM[i][j]= accuracy_score(y_test, predictions)
            
            clf_svm[j].fit(Z_train, y_train) #pca
            predictions = clf_svm[j].predict(Z_test)
            SVM_pca[i][j]= accuracy_score(y_test, predictions)

#MLPClassifier
    MLP= np.zeros((2,2))
    MLP_pca = np.zeros((2,2))
    hidden_layers = (h,)
    activation = ['logistic','relu']
    solver = ['adam','sgd']
    for i in range(2):
        for j in range(2):
            opts = dict(hidden_layer_sizes = hidden_layers, verbose = True, \
            activation = activation[i], tol = 1e-6, max_iter = int(1e6))
            clf_MLP = MLPClassifier(solver = solver[j], **opts)
            clf_MLP.fit(X_train, y_train)
            predictions_mlp = clf_MLP.predict(X_test)
            MLP[i][j]= accuracy_score(y_test, predictions_mlp)

            clf_MLP.fit(Z_train, y_train) #pca
            predictions_mlp = clf_MLP.predict(Z_test)
            MLP_pca[i][j]= accuracy_score(y_test, predictions_mlp)

    return data,LR,SVM,MLP,LR_pca,SVM_pca,MLP_pca

In [3]:
# Read data
df = pd.read_csv("face_data.csv")
X = np.array(df.drop('target',axis=1))
y = np.array(df['target'])


indices = np.random.permutation(X.shape[0])
_X = X[indices[:100], :]
_y = y[indices[:100]]
print(_y)

[24 10  8 23 17 14 17  6 39  1 29 16 16  4  0 12 28  1 17 37 15 26 23 20
 29  1  0 14 37 17 34  2 19 36  2  5  3 15 21 21  7 25 39 22 25 37 19 38
 16 17 15  7 34 15 26 25 15  5 20 22 23  4  3 39 19 38 11 36  8 11  5 27
 38  2  6  7 27 22 21 10 14 22  8  2  0 20 27 12  5 18 11 15 17  4  8  1
 27  3 16  7]


In [4]:
data,LR,SVM,MLP,LR_pca,SVM_pca,MLP_pca =classifier(X,y,"face_data.csv",30)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   14.7s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s finished


[LibLinear][LibLinear]

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    7.7s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    1.0s finished
c:\Users\ian20\anaconda3\lib\site-packages\sklearn\svm\_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=1000000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
c:\Users\ian20\anaconda3\lib\site-packages\sklearn\svm\_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=1000000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
c:\Users\ian20\anaconda3\lib\site-packages\sklearn\svm\_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=1000000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
c:\Users\ian20\anaconda3\lib\sit

Iteration 1, loss = 3.73243166
Iteration 2, loss = 3.68327014
Iteration 3, loss = 3.66693606
Iteration 4, loss = 3.65174533
Iteration 5, loss = 3.63845804
Iteration 6, loss = 3.62456778
Iteration 7, loss = 3.60797768
Iteration 8, loss = 3.59386109
Iteration 9, loss = 3.58084231
Iteration 10, loss = 3.56854001
Iteration 11, loss = 3.55736218
Iteration 12, loss = 3.54595287
Iteration 13, loss = 3.53608876
Iteration 14, loss = 3.52253794
Iteration 15, loss = 3.51047917
Iteration 16, loss = 3.49800932
Iteration 17, loss = 3.48881576
Iteration 18, loss = 3.47711980
Iteration 19, loss = 3.46606390
Iteration 20, loss = 3.45791721
Iteration 21, loss = 3.44628740
Iteration 22, loss = 3.43717902
Iteration 23, loss = 3.42485343
Iteration 24, loss = 3.41448324
Iteration 25, loss = 3.40326027
Iteration 26, loss = 3.39314995
Iteration 27, loss = 3.38358667
Iteration 28, loss = 3.37490307
Iteration 29, loss = 3.36372089
Iteration 30, loss = 3.35228062
Iteration 31, loss = 3.34333474
Iteration 32, los

In [5]:
print("dataname = ",data,"\n","LR = ",LR,"\n","SVM= ",SVM,"\n","MLP= ",MLP,\
      "\n--------------\n",\
      "LR_pca= ",LR_pca,"\n","SVM_pca= ",SVM_pca,"\n","MLP_pca= ",MLP_pca)

dataname =  face_data.csv 
 LR =  [0.9625 0.9    0.9625] 
 SVM=  [[0.95 0.   0.  ]
 [0.95 0.   0.  ]] 
 MLP=  [[0.95   0.975 ]
 [0.15   0.9375]] 
--------------
 LR_pca=  [0.1    0.0625 0.1   ] 
 SVM_pca=  [[0.1625 0.1125 0.1875]
 [0.1625 0.1125 0.1875]] 
 MLP_pca=  [[0.1625 0.1375]
 [0.15   0.15  ]]


In [2]:
acc = {'LR': [0.9625, 0.0625],
        'SVM': [ 0.95, 0.1875 ],
        'MLP': [0.975,0.1625]       
        }
index = ['original', 'pca']
df = pd.DataFrame(acc, index=index)
df

LR     SVM     MLP
original  0.9625  0.9500  0.9750
pca       0.0625  0.1875  0.1625

In [11]:
# Split data into training and testing data 7:3
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.20) 
# Standardize data
scaler = StandardScaler()
X_train_ = scaler.fit_transform(X_train)
X_test_ = scaler.fit_transform(X_test)


 # SVM
SVM_pca=np.zeros((2,3))
C = 1 # SVM regularization parameter
opts = [dict(C = C, tol = 1e-6, max_iter = int(1e6)),dict(C = C, decision_function_shape = 'ovo', tol = 1e-6, max_iter = int(1e6))]
n=[2,5,10]    
for i in range(2):
    for j in range(len(n)):
        #PCA
        pca = PCA(n_components = n[j]).fit(X_train_)
        Z_train = pca.transform(X_train_)
        Z_test = pca.transform(X_test_)

        clf_svm = SVC(kernel="poly", degree=3, gamma="auto", **opts[i]) 
        clf_svm.fit(X_train, y_train)
          
        clf_svm.fit(Z_train, y_train) #pca
        predictions = clf_svm.predict(Z_test)
        SVM_pca[i][j]= accuracy_score(y_test, predictions)
print(SVM_pca)

c:\Users\ian20\anaconda3\lib\site-packages\sklearn\svm\_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=1000000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
c:\Users\ian20\anaconda3\lib\site-packages\sklearn\svm\_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=1000000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(


[[0.2375 0.625  0.8375]
 [0.2625 0.625  0.8375]]


<h3>實驗結果觀察</h3>
根據以上實驗結果，當 n_components＝2 時，可以發現沒有做PCA的資料集正確率比有做PCA的資料集來得高許多，且對於沒有做PCA的資料集來說，邏輯斯迴歸在所有參數中接有很高的正確率，SVM在 kernel="linear" 時有突出的正確率表現，MLP則是除了在 activation='relu'、solver='adam' 時表現不佳之外，在其他三種參數的搭配下皆有良好的表現，其中在 activation='logistic'、solver='sgd' 時有達到0.975的最高正確率。<br>
由於觀察到進行過PCA的資料集在 kernel="poly" 的SVM模型中，有稍高的正確率，因此多做了一項實驗，發現當 n_components 取到10時，正確率可以達到0.8，最後發現能夠藉由增加 n_components 數量來有效率的建立預測模型。